### Use embeddings

In this tutorial, we'll use product group embeddings to compare a customer's latest invoice with their past purchases from the last 26 weeks.

To learn how to create a SQL Embedding User-Defined Function (UDF), check out the ['Bring Your Own Transformer' tutorials](https://docs.featurebyte.com/latest/get_started/bring_your_own_transformer/overview/).

For our hosted tutorials, we have pre-configured a SQL UDF using the SBERT Transformer model on our Snowflake data warehouse. We'll register this UDF in the Catalog and apply it to analyze the ProductGroup descriptions.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

15:32:17 | INFO     | SDK version: 1.0.2.dev46


15:32:17 | INFO     | No catalog activated.


15:32:17 | INFO     | Using profile: tutorial


15:32:17 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


15:32:17 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


15:32:17 | INFO     | SDK version: 1.0.2.dev46


15:32:17 | INFO     | No catalog activated.


15:32:17 | INFO     | Catalog activated: Grocery Dataset Tutorial


#### Register the F_SBERT_EMBEDDING UDF to the Catalog

In [2]:
fb.UserDefinedFunction.create(
    name='embedding', 
    sql_function_name='F_SBERT_EMBEDDING',
    function_parameters=[fb.FunctionParameter(name="x", dtype=fb.enum.DBVarType.VARCHAR)],
    output_dtype=fb.enum.DBVarType.ARRAY,
    is_global=False,
)

<featurebyte.api.user_defined_function.UserDefinedFunction at 0x1686d7bb0>
{
  'name': 'embedding',
  'created_at': '2024-04-26T07:32:17.883000',
  'updated_at': None,
  'description': None,
  'sql_function_name': 'F_SBERT_EMBEDDING',
  'function_parameters': [
    {
      'name': 'x',
      'dtype': 'VARCHAR',
      'default_value': None,
      'test_value': None
    }
  ],
  'signature': 'embedding(x: str) -> array',
  'output_dtype': 'ARRAY',
  'feature_store_name': 'playground',
  'used_by_features': []
}

#### Apply the embedding UDF instance to ProductGroup

In [3]:
# Get embedding UDF instance.
embedding_udf = catalog.get_user_defined_function(
    "embedding"
)

In [4]:
# Get view from GROCERYPRODUCT dimension table.
groceryproduct_view = catalog.get_view("GROCERYPRODUCT")
# Apply embedding to ProductGroup column in GROCERYPRODUCT view.
groceryproduct_view["ProductGroup_embedding"] = embedding_udf(groceryproduct_view["ProductGroup"])

#### Get other views

In [5]:
# Get view from GROCERYINVOICE event table.
groceryinvoice_view = catalog.get_view("GROCERYINVOICE")
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")

#### Join views

In [6]:
# Join GROCERYPRODUCT view to INVOICEITEMS view.
invoiceitems_view = invoiceitems_view.join(
    groceryproduct_view, rprefix="product_"
)

#### Get the mean vector of an invoice's Product Group descriptions

In [7]:
# Group invoiceitems_view by invoice entity (GroceryInvoiceGuid).
invoiceitems_view_by_invoice =\
invoiceitems_view.groupby("GroceryInvoiceGuid")

In [8]:
# Mean vector of product_ProductGroup_embedding for the invoice.
invoice_mean_vector_of_item_product_productgroup_embedding =\
invoiceitems_view_by_invoice.aggregate(
    "product_ProductGroup_embedding", method=fb.AggFunc.AVG,
    feature_name="INVOICE_Mean_vector_of_item_product_ProductGroup_embedding"
)

#### Get the mean vector of the Customer's latest invoice

In [9]:
# Add INVOICE_Mean_vector_of_item_product_ProductGroup_embedding feature to the GROCERYINVOICE view
# as a column.
groceryinvoice_view =\
groceryinvoice_view.add_feature(
    "INVOICE_Mean_vector_of_item_product_ProductGroup_embedding",
    invoice_mean_vector_of_item_product_productgroup_embedding
)

In [10]:
# Group GROCERYINVOICE view by customer entity (GroceryCustomerGuid).
groceryinvoice_view_by_customer =\
groceryinvoice_view.groupby(['GroceryCustomerGuid'])

In [11]:
# Get Latest Mean vector of item product_ProductGroup_embedding for the customer
customer_latest_invoice_mean_vector_of_item_product_productgroup_embedding =\
groceryinvoice_view_by_customer.aggregate_over(
    "INVOICE_Mean_vector_of_item_product_ProductGroup_embedding", method="latest",
    feature_names=["CUSTOMER_Latest_INVOICE_Mean_vector_of_item_product_ProductGroup_embedding"],
    windows=[None]
)["CUSTOMER_Latest_INVOICE_Mean_vector_of_item_product_ProductGroup_embedding"]

#### Get the mean vector for the Customer's Product Group descriptions over past 26 weeks

In [12]:
# Group INVOICEITEMS view by customer entity (GroceryCustomerGuid).
invoiceitems_view_by_customer =\
invoiceitems_view.groupby(['GroceryCustomerGuid'])

In [13]:
# Get Mean vector of product_ProductGroup_embedding for the customer over time.
feature_group =\
invoiceitems_view_by_customer.aggregate_over(
    "product_ProductGroup_embedding", method="avg",
    feature_names=[
        "CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w"
    ],
    windows=["26w"],
)
# Get CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w object from feature group.
customer_mean_vector_of_item_product_productgroup_embedding_26w =\
feature_group["CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w"]

#### Derive Similarity between latest invoice and 26 weeks purchases

In [14]:
# Derive Similarity feature from cosine similarity between
# CUSTOMER_Latest_INVOICE_Mean_vector_of_item_product_ProductGroup_embedding
# and CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w
customer_mean_vector_of_item_product_productgroup_embedding_26w_vs_latest_invoice =\
customer_latest_invoice_mean_vector_of_item_product_productgroup_embedding.vec.cosine_similarity(
    customer_mean_vector_of_item_product_productgroup_embedding_26w
)
# Give a name to new feature
customer_mean_vector_of_item_product_productgroup_embedding_26w_vs_latest_invoice.name = \
"CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w_vs_latest_invoice"

#### Preview feature

In [15]:
# Get observation table: 'Preview Table with 10 items'
preview_table = catalog.get_observation_table("Preview Table with 10 items")

In [16]:
# Preview customer_mean_vector_of_item_product_productgroup_embedding_26w
customer_mean_vector_of_item_product_productgroup_embedding_26w.preview(
    preview_table
)

POINT_IN_TIME                GROCERYINVOICEITEMGUID  \
0 2022-10-05 14:30:03  fc4769cf-41d6-4fb0-9cfc-fe30502cfa18   
1 2022-11-09 18:07:20  37122b82-478b-4d9e-b236-69629b592c0b   
2 2023-04-19 15:25:05  8a60f455-aff1-4b4e-8c63-9ab89df2715d   
3 2022-08-16 15:37:21  6781acc6-652d-4867-a138-2d8adb278886   
4 2023-03-13 21:11:43  cfc620a2-0054-4b4b-99d5-040cf87cfe2d   
5 2023-03-19 15:22:18  dcdb7c98-dd62-4287-b432-bfe3a2317ebc   
6 2023-02-27 13:27:47  b807e05c-ff1c-4fb3-a760-e0e8ce29c859   
7 2023-02-15 21:10:22  5daf8edb-8625-4653-aaa0-9ac03df92017   
8 2022-11-03 14:39:00  9faf5936-d4bb-4709-a530-c1624ec003a5   
9 2022-11-18 10:07:49  ae2ccf38-4e5d-4c76-b1e5-04f12307e45b   

  CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w  
0  [-0.050867025223711004, 0.036183445178904004, ...               
1  [-0.051389772166006, 0.034165915842724, -0.020...               
2  [-0.052858197418672, 0.028179515303383, -0.013...               
3  [-0.055149581778464005, 0.03823821472676, -0.0...               
4  [-0.052533533882473005, 0.03202685306233, -0.0...               
5  [-0.049488712660913, 0.034617167088656, -0.022...               
6  [-0.056006776304074, 0.031965939343047, -0.004...               
7  [-0.043588562243401005, 0.022270886707502, -0....               
8  [-0.051126038899557004, 0.024472378865799, -0....               
9  [-0.047493995182696, 0.034784211601623004, -0....

In [17]:
# Preview customer_mean_vector_of_item_product_productgroup_embedding_26w_vs_latest_invoice
customer_mean_vector_of_item_product_productgroup_embedding_26w_vs_latest_invoice.preview(
    preview_table
)

POINT_IN_TIME                GROCERYINVOICEITEMGUID  \
0 2022-11-03 14:39:00  9faf5936-d4bb-4709-a530-c1624ec003a5   
1 2022-08-16 15:37:21  6781acc6-652d-4867-a138-2d8adb278886   
2 2022-10-05 14:30:03  fc4769cf-41d6-4fb0-9cfc-fe30502cfa18   
3 2023-03-19 15:22:18  dcdb7c98-dd62-4287-b432-bfe3a2317ebc   
4 2022-11-18 10:07:49  ae2ccf38-4e5d-4c76-b1e5-04f12307e45b   
5 2023-03-13 21:11:43  cfc620a2-0054-4b4b-99d5-040cf87cfe2d   
6 2022-11-09 18:07:20  37122b82-478b-4d9e-b236-69629b592c0b   
7 2023-02-15 21:10:22  5daf8edb-8625-4653-aaa0-9ac03df92017   
8 2023-02-27 13:27:47  b807e05c-ff1c-4fb3-a760-e0e8ce29c859   
9 2023-04-19 15:25:05  8a60f455-aff1-4b4e-8c63-9ab89df2715d   

   CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w_vs_latest_invoice  
0                                           0.383319                                  
1                                           0.657974                                  
2                                           0.812872                                  
3                                           0.885103                                  
4                                           0.460290                                  
5                                           0.611533                                  
6                                           0.964328                                  
7                                           0.776228                                  
8                                           0.778742                                  
9                                           0.549239

#### Save feature

In [18]:
# Save feature
customer_mean_vector_of_item_product_productgroup_embedding_26w_vs_latest_invoice.save()

Working... |                                        | ▁▃▅ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▂▄▆ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▃▅▇ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▄▆█ 0% in 0s (~0s, 0.0%/s)

Working... |                                        | ▅▇▇ 0% in 0s (~0s, 0.0%/s)

...

Working... |████████████████████████████████████████| ▆▄▂ 100% in 6s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▅▃▁ 100% in 6s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▄▂▂ 100% in 6s (~0s, 0.2%/

Working... |████████████████████████████████████████| ▃▁▃ 100% in 6s (~0s, 0.2%/

Done! |████████████████████████████████████████| 100% in 6.2s (0.16%/s)         

#### As always, add description and view definition file

In [19]:
# Add description
customer_mean_vector_of_item_product_productgroup_embedding_26w_vs_latest_invoice.update_description(
	"Compare the customer's 4w Mean vector of item "
	"product_ProductGroup_embedding with the customer's most recent "
	"invoice. This comparison is done using the Cosine Similarity metric to"
	" measure how similar these mean vector embeddings are."
)
# See feature definition file
customer_mean_vector_of_item_product_productgroup_embedding_26w_vs_latest_invoice.definition

'# Generated by SDK version: 1.0.2.dev46\nfrom bson import ObjectId\nfrom featurebyte import DimensionTable\nfrom featurebyte import EventTable\nfrom featurebyte import FeatureJobSetting\nfrom featurebyte import ItemTable\nfrom featurebyte import UserDefinedFunction\n\n\n# dimension_table name: "GROCERYPRODUCT"\ndimension_table = DimensionTable.get_by_id(ObjectId("662b577aaa13c89fa14554e3"))\ndimension_view = dimension_table.get_view(\n    view_mode="manual", drop_column_names=[], column_cleaning_operations=[]\n)\ncol = dimension_view["ProductGroup"]\n\n# udf_name: embedding, sql_function_name: F_SBERT_EMBEDDING\nudf_embedding = UserDefinedFunction.get_by_id(\n    ObjectId("662b58815827fd6e8d7545f9")\n)\ncol_1 = udf_embedding(col)\nview = dimension_view.copy()\nview["ProductGroup_embedding"] = col_1\n\n# item_table name: "INVOICEITEMS", event_table name: "GROCERYINVOICE"\nitem_table = ItemTable.get_by_id(ObjectId("662b5778aa13c89fa14554e2"))\nitem_view = item_table.get_view(\n    event_suffix=None,\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n    event_drop_column_names=["record_available_at"],\n    event_column_cleaning_operations=[],\n    event_join_column_names=[\n        "Timestamp",\n        "GroceryInvoiceGuid",\n        "GroceryCustomerGuid",\n        "tz_offset",\n    ],\n)\njoined_view = item_view.join(\n    view, on="GroceryProductGuid", how="left", rsuffix="", rprefix="product_"\n)\nfeat = joined_view.groupby(\n    by_keys=["GroceryInvoiceGuid"], category=None\n).aggregate(\n    value_column="product_ProductGroup_embedding",\n    method="avg",\n    feature_name="INVOICE_Mean_vector_of_item_product_ProductGroup_embedding",\n    skip_fill_na=True,\n)\n\n# event_table name: "GROCERYINVOICE"\nevent_table = EventTable.get_by_id(ObjectId("662b5775aa13c89fa14554e1"))\nevent_view = event_table.get_view(\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n)\njoined_view_1 = event_view.add_feature(\n    new_column_name="INVOICE_Mean_vector_of_item_product_ProductGroup_embedding",\n    feature=feat,\n    entity_column="GroceryInvoiceGuid",\n)\ngrouped = joined_view_1.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="INVOICE_Mean_vector_of_item_product_ProductGroup_embedding",\n    method="latest",\n    windows=[None],\n    feature_names=[\n        "CUSTOMER_Latest_INVOICE_Mean_vector_of_item_product_ProductGroup_embedding"\n    ],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat_1 = grouped[\n    "CUSTOMER_Latest_INVOICE_Mean_vector_of_item_product_ProductGroup_embedding"\n]\ngrouped_1 = joined_view.groupby(\n    by_keys=["GroceryCustomerGuid"], category=None\n).aggregate_over(\n    value_column="product_ProductGroup_embedding",\n    method="avg",\n    windows=["26w"],\n    feature_names=[\n        "CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w"\n    ],\n    feature_job_setting=FeatureJobSetting(\n        blind_spot="120s", frequency="3600s", time_modulo_frequency="120s"\n    ),\n    skip_fill_na=True,\n)\nfeat_2 = grouped_1[\n    "CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w"\n]\nfeat_3 = feat_1.vec.cosine_similarity(other=feat_2)\nfeat_3.name = "CUSTOMER_Mean_vector_of_item_product_ProductGroup_embedding_26w_vs_latest_invoice"\noutput = feat_3\noutput.save(_id=ObjectId("662b58875827fd6e8d7545fe"))\n'

### Concepts in this tutorial
- [View Joins](https://docs.featurebyte.com/latest/about/glossary/#view-join)
- [UDF Transforms](https://docs.featurebyte.com/latest/about/glossary/#udf-transforms)
- [Feature Transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)

#### SDK reference for
- [Get UDF instance](https://docs.featurebyte.com/latest/reference/featurebyte.api.catalog.Catalog.get_user_defined_function/)
- [Add an aggregation by invoice to the event view](https://docs.featurebyte.com/latest/reference/featurebyte.api.event_view.EventView.add_feature/)
- [Feature.vec.cosine_similarity()](https://docs.featurebyte.com/latest/reference/featurebyte.Feature.vec.cosine_similarity/)
